In [1]:


import time
import gymnasium
from miniwob.action import ActionTypes
from dom_processing import iterate_dom, dict2html, prepare_t5_input
from inference_points import infer_remote_model, parse_t5_output_action
from cc_net5_tokenizer import CCNeT5Tokenizer
from cosine_similarity import find_closest_embeddings
import torch
import numpy as np
import json


/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/gymnasium/envs/registration.py:521: UserWarning: WARN: Overriding environment miniwob/bisect-angle-v1 already in registry.
  logger.warn(f"Overriding environment {new_spec.id} already in registry.")
/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/gymnasium/envs/registration.py:521: UserWarning: WARN: Overriding environment miniwob/book-flight-v1 already in registry.
  logger.warn(f"Overriding environment {new_spec.id} already in registry.")
/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/gymnasium/envs/registration.py:521: UserWarning: WARN: Overriding environment miniwob/book-flight-nodelay-v1 already in registry.
  logger.warn(f"Overriding environment {new_spec.id} already in registry.")
/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/gymnasium/envs/registration.py:521: UserWarning: WARN: Overriding environment miniwob

In [2]:


# We remove all elements not needed in the received html to have it cleaned
def clean_html(html):
    tag_remove = ['script', 'img', 'meta', 'head', '<head', 'html', 'link', 'title', 'line', '!--', '!---']
    parts = html.replace('  ', '').split('\n')
    clean_html = ""
    for p in parts:
        if '<' in p:
            # check for tag
            tag = p.split('<')[1].split('>')[0].replace('/', '').split(' ')[0]
            if not tag in tag_remove:
                #print(tag)
                clean_html += p

    return clean_html

drop_fields = ['children', 'tag', 'onmousemove', 'onclick', 'onscroll', 'ontouchmove', 'ontouchstart', 'ontouchend', 'onkeypress', 'children', 'bgColor', 'width', 'height', 'focused', 'fgColor', 'right', 'top', 'left', 'bottom', 'class', 'classes']

# Converts the html to a string
def html2string(element):
    html_conct = "<" + element['tag']

    # add fields
    for field in element:
        if not field in drop_fields and field != "text":
            html_conct += ' ' + field + '="' + element[field] + '"'
    html_conct += '>'

    # add text
    html_conct += element['text']

    # If the element doesn't match, recursively search its children
    if "children" in element:
        for i, child in enumerate(element["children"]):
            path = html2string(child)
            html_conct += path

    html_conct += '</' + element['tag'] + '>'

    return html_conct

def build_tree(element):
        result = {"tag": element.tag}

        # Adding attributes as key-value pairs to the element
        if element.attrib:
            result.update({k: v for k, v in element.attrib.items()})

        # Adding text
        text = element.text.strip() if element.text else ""
        result['text'] = text

        # Adding child elements as nested dictionaries
        if len(element) > 0:
            result["children"] = [build_tree(child) for child in element]

        return result

from lxml import etree
parser = etree.HTMLParser()
def html2dict(html_str):
    tree = etree.fromstring(html_str, parser)# Starting from the root element and building the tree
    root = tree.getroottree().getroot()
    result = build_tree(root)
    return result

# Find whether <canvas> appears before or after the wrap
def wrapCanvasDist(html):
    canvas = len(html.split('<canvas')[0])
    wrap = len(html.split('id="wrap')[0])
    return wrap < canvas

def find_element_path2(element, attributes):
    # Check if the current element matches the attributes
    if all(attr in element.items() for attr in attributes.items()):
        return [element["tag"]]

    # If the element doesn't match, recursively search its children
    if "children" in element:
        for i, child in enumerate(element["children"]):
            path = find_element_path2(child, attributes)
            if path is not None:
                #print(f'element: {element["tag"]}, i:{i}, path:{path}')
                #return [element["tag"] , f"{i+1}/{len(element['children'])}"] + path
                return [element["tag"] , f"{i+1}"] + path
    # If no match was found, return None
    return None

# Update the mapping dictionary of ref with page changes
def update_ref2_random(old_dict, old_rand2ref, new_dict):
    _remvoved_refs_keys = old_dict.keys() - new_dict.keys()
    added_refs_keys = new_dict.keys() - old_dict.keys() # no use of old refs, better to keep them in old_dict

    # create subset_dictionary
    added_refs = {}
    for added_ref in added_refs_keys:
        if added_ref in old_dict.keys():
            added_refs[added_ref] = old_dict[added_ref]
        else:
            added_refs[added_ref] = new_dict[added_ref]

    # attribute random to new refs:
    added_refs_dict, added_rand2refs = randomize_ref_dict(list(added_refs.keys()))

    # Update the old dictionary with the new mapping
    old_dict.update(added_refs_dict)
    old_rand2ref.update(added_rand2refs)

    # These are the new mappings
    return old_dict, old_rand2ref

import random

# find all refs of the dom dict
def find_all_refs(dom):
    refs = []
    if 'ref' in dom.keys():
        refs.append(dom['ref'])
    if 'children' in dom.keys():
        for child in dom['children']:
            f_ref = find_all_refs(child)
            refs += f_ref
    return list(set(refs))

# provide ref list and return dictionary with randomized values
# also return dict to reconstruct it all
def randomize_ref_dict(refs):
    entries = refs.copy()
    random.shuffle(entries)
    ref_dict = {}
    for i, k in enumerate(refs):
        ref_dict[k] = entries[i]

    ref2rand = ref_dict
    rand2ref = {}
    for k in ref2rand.keys():
        rand2ref[ref2rand[k]] = k
    return ref_dict, rand2ref

# Assigns the randomized value to each ref of the dom dict
def attribute_random_refs_dom(dom, refs):
    if 'ref' in dom.keys():
        dom['ref'] = refs[dom['ref']]
    if 'children' in dom.keys():
        new_children = []
        for child in dom['children']:
            new_child = attribute_random_refs_dom(child, refs)
            new_children.append(new_child)
        dom['children'] = new_children
    return dom

def convert_to_nested_dict(elements):
    # Create a dictionary to store elements by their 'ref' value
    element_dict = {element['ref']: element for element in elements}

    # Iterate through the elements to build the nested structure
    for element in elements:
        parent_ref = element['parent']
        if parent_ref != 0:
            parent_element = element_dict.get(parent_ref)
            if 'children' not in parent_element:
                parent_element['children'] = []
            if 'children' not in element:
                # Empty children field
                element['children'] = []
            parent_element['children'].append(element)

    # Find the root element (element with 'parent' = 0)
    root_element = None
    for element in elements:
        if element['parent'] == 0:
            root_element = element
            break

    return root_element

In [3]:
import requests
import json
import random

# Infer the model to generate a plan
def call_T5_planning(utterance):
    t5_input = 'Devise a plan for the following instruction: ' + utterance
    print(f"{t5_input}")
    t5_output = infer_remote_model(t5_input, t5_url + '/infer_t5_old_payload')['prediction']
    print(f'received output: {t5_output}')
    return t5_output


def call_T5_hierarchy(action_history, utterance, dom):
    html_str = dict2html(dom)
    t5_input = prepare_t5_input(action_history, utterance, html_str)
    print(f't5_input: {t5_input}')
    t5_output = infer_remote_model(t5_input, t5_url + '/infer_t5_old_payload')
    parts = t5_output['prediction'].split(',')
    t5_action = parts[0].replace(';', '')
    try:
        t5_ref = int(parts[1].replace(' ', '').replace(',', ''))
        t5_keydown = ''.join(parts[2])
        if len(parts)>3:
            done = parts[3].replace(' ', '') == 'done'
        else:
            done = ""
    except Exception as e:
        print(f'issue parsing T5 output: {parts}')
        t5_ref = 0
        t5_keydown = ''
        done = ''

    return t5_action, t5_ref, t5_keydown, done

def parse_t5_parts(parts):
    t5_action = parts[0].replace(';', '')
    try:
        t5_ref = int(parts[1].replace(' ', '').replace(',', ''))
        t5_keydown = ''.join(parts[2])
        if len(parts)>3:
            done = parts[3].replace(' ', '') == 'done'
        else:
            done = ""
    except Exception as e:
        print(f'issue parsing T5 output: {parts}')
        t5_ref = 0
        t5_keydown = ''
        done = ''
    return t5_action, t5_ref, t5_keydown, done

def inference_model_T5_self_discard(instruction):
    #payload = {'instruction_input': instruction}
    print(f'about to make request: {instruction}')
    headers = {'Content-Type': 'application/json'}
    response = requests.post(t5_url+'/infer_t5_old_payload', data=json.dumps(instruction), headers=headers).json()['prediction']
    parts = response.split(',')
    t5_action = parts[0].replace(';', '')
    try:
        t5_ref = int(parts[1].replace(' ', '').replace(',', ''))
        t5_keydown = ''.join(parts[2])
        if len(parts)>3:
            done = parts[3].replace(' ', '') == 'done'
        else:
            done = ""
    except Exception as e:
        print(f'issue parsing T5 output: {parts}')
        t5_ref = 0
        t5_keydown = ''
        done = ''
    return t5_action, t5_ref, t5_keydown, done

def inference_model_T5_self(instruction):
    #payload = {'instruction_input': instruction}
    #print(f'about to make request: {payload}')
    headers = {'Content-Type': 'application/json'}
    response = requests.post(t5_url+'/infer_t5_old_payload', data=json.dumps(instruction), headers=headers)
    return response.json()


model_endpoints = 'https://ff81-92-177-9-116.ngrok-free.app/'
t5_url = 'https://ff81-92-177-9-116.ngrok-free.app/'
t5_url = model_endpoints

In [4]:
# 1 - Get out Tokenizer Class
css_fields = ['top', 'left', 'width', 'height']
special_characters = ['.', ',', '#', ':', '-', '/', '(', ')', 'https://', '@', '&', '"', "'", '!', '?', ';', '+', '=',
                      '*', '$', '€', '*', '`']

def round_to_nearest_ten(number):
    return round(number / 10) * 10

import torch

# Turn it into a class
class CCNeT5Tokenizer:
    def __init__(self, vocab_path):
        stoi = {}
        itos = {}
        self.padding_char = '<PAD>'
        self.special_characters = ['.', ',', '#', ':', '-', '/', '(', ')', 'https://', '@', '&', '"', "'", '!', '?',
                                   ';', '+', '=', '*', '$', '€', '*', '`']

        with open(vocab_path, 'r') as file:
            for index, line in enumerate(file):
                line = line.strip()
                stoi[line] = index
                itos[index] = line

        stoi[' '] = stoi['']
        itos[stoi[' ']] = ' '
        self.stoi = stoi
        self.stoi[self.padding_char] = len(stoi.keys())-1  # Add PADDING character
        # We do not need itos as we don't implement a de-tokinezing function.
        self.itos = itos
        self.itos[len(stoi.keys()) - 2] = self.padding_char  # Add PADDING character
        print(f'pad: {len(stoi.keys()) - 2}')
        print(f'Loaded CC_NeT5 Tokenizer with vocabulary size being {len(self.stoi)}.')

        # Instantiate the embedding function
        vocab_size = len(stoi)

    # Provide a string and tokenize it: utterance or task name.
    def tokenize_string(self, string):
        tokenized_string = []
        for w in str(string).lower().split(' '):
            for sc in self.special_characters:
                if sc in w:
                    w = w.replace(sc, 'Ø' + sc + 'Ø')
            p1_words = [s for s in w.split('Ø') if s != '']
            # Check if the found words exist in our vocab, else subdivide
            for fw in p1_words:
                if fw not in self.stoi.keys():
                    for c in fw:
                        tokenized_string.append(self.stoi[c])
                else:
                    tokenized_string.append(self.stoi[fw])
        return tokenized_string

    # Turns an array into a string
    def detokenize_array(self, array):
        reconstruted_string = []
        #pad_index = self.itos[self.stoi[self.padding_char]]
        for v in array:
            v = int(v)
            s = self.itos[v]
            if s != self.padding_char:
                reconstruted_string.append(s)

        #reconstruted_string = ' '.join(reconstruted_string)
        cleaned_string = ''
        last_single = False
        for s in reconstruted_string:
            if len(s) > 1:
                if last_single:
                    cleaned_string += ' '
                    last_single = False
                cleaned_string += s + ' '
            else:
                # We do this to treat single length characters
                cleaned_string += s
                last_single = True
        return cleaned_string

    # Truncate and pad the incoming sentences based on a max_size argument
    def truncate_pad_entry(self, tokenized_array, max_size):
        if len(tokenized_array) < max_size:
            while len(tokenized_array) < max_size:
                tokenized_array.append(self.stoi[self.padding_char])
            return tokenized_array
        elif len(tokenized_array) > max_size:
            # Too long, so we automatically truncate
            return tokenized_array[:max_size]
        else:
            # Just avoid iterating under the hood
            return tokenized_array

    # Tokenize a DOM dictionary
    def tokenize_dom(self, dom):
        tokenized_dom = []

        # Add opening tag
        element_tag = dom['tag'].lower()
        if 'input' in dom.keys():
            # if tag is input, reformat it
            element_tag = dom['input'].lower() + '_' + dom['type'].lower()
            tokenized_dom.append(self.stoi['<' + element_tag])
        else:
            # add normal tag
            try:
                tokenized_dom.append(self.stoi['<' + dom['tag'].lower()])
            except:
                tokenized_dom.append(self.stoi['<div'])

        for field in dom:
            if field != 'tag' and field != 'children' and field != 'type' and field != 'text' and field not in css_fields:  # and field != 'value':

                tokenized_dom.append(self.stoi[field.lower()])

                # Ensure we don't have float values, we'll stick with integers
                if isinstance(dom[field], float):
                    tokenized_dom.append(self.stoi[str(int(round_to_nearest_ten(dom[field])))])
                else:
                    words = str(dom[field]).lower().split(' ')
                    for word in words:
                        for sc in special_characters:
                            if sc in word:
                                word = word.replace(sc, 'Ø' + sc + 'Ø')
                        p1_words = [s for s in word.split('Ø') if s != '']

                        # decides whether we keep the full word, or just the letters:
                        if field == 'value' or (False and (field == 'label' or field == 'button')):
                            for w in p1_words:
                                # Take individual characters of the value string
                                processed_words = [self.stoi[w[i:i + 1]] for i in range(0, len(w), 1)]
                                tokenized_dom += processed_words

                        elif field == 'ref':
                            for w in p1_words:
                                # Take individual characters of the value string
                                processed_words = [self.stoi[w[i:i + 3]] for i in range(0, len(w), 3)]
                                tokenized_dom += processed_words
                        else:
                            # Use the full word:
                            for w in p1_words:
                                try:
                                    tokenized_dom.append(self.stoi[str(w)])
                                except:
                                    # split the word by char
                                    for s in str(w):
                                        try:
                                            tokenized_dom.append(self.stoi[s])
                                        except Exception as e:
                                            print(f'Not recognized char: {e}')
                                            continue

            elif field == 'text':
                tokenized_dom.append(self.stoi['text'])
                for c in dom[field]:
                    tokenized_dom.append(self.stoi[c])
            elif field in css_fields:
                # Cast field
                tokenized_dom.append(self.stoi[field])
                css_value = int(round_to_nearest_ten(float(dom[field])))
                tokenized_dom.append(self.stoi[str(css_value)])

        if 'children' in dom.keys():
            tokenized_dom.append(self.stoi['children'])
            for child in dom['children']:
                tokenized_dom += self.tokenize_dom(child)
                # for v in found_vocab:
                #    tokenized_dom.append(self.stoi[v])

        # add closing tag
        try:
            tokenized_dom.append(self.stoi['</' + element_tag + '>'])
        except:
            tokenized_dom.append(self.stoi['</div>'])

        return tokenized_dom

def format_image(image):
    rgb_data = np.transpose(np.array(image) / 255.0, (2, 0, 1))
    return rgb_data

def format_language_rgb_input(rgb_data, dom_data, utterance_data, task_data):
    # Put language task together
    language_input = np.concatenate((dom_data, utterance_data, task_data))
    #language_input = dom_data
    print(language_input.shape)

    rgb_data = torch.from_numpy(rgb_data).type(torch.float32)
    language_input = torch.from_numpy(language_input).type(torch.long)
    return rgb_data, language_input

vocab_path="vocab.txt"
tokenizer = CCNeT5Tokenizer(vocab_path=vocab_path)

pad: 1590
Loaded CC_NeT5 Tokenizer with vocabulary size being 1592.


In [19]:
# turn action output into tensor length 10
def action2tensor(tokenizer, action_type, ref, keydown):
    data = []

    if action_type == 'click':
        data.append(0)
    else:
        data.append(1)

    # append ref
    if int(ref) < 0:
        data.append(0)
    elif int(ref)>500:
        data.append(500)
    else:
        data.append(int(ref))
    tokenized_keydown = tokenizer.truncate_pad_entry(tokenizer.tokenize_string(keydown), 8)
    data += tokenized_keydown
    return np.array(data)

import json
def prepare_ccnet5_payload(rgb_data, language_input, previous_action, t5_output_tensor):
    cc_net5_payload = {
        'rgb_data': rgb_data,
        'language_data': language_input,
        'previous_action': previous_action,
        't5_output': t5_output_tensor,
    }
    cc_net5_payload_numpy = {
        key: value.detach().numpy().tolist() if isinstance(value, torch.Tensor) else value
        for key, value in cc_net5_payload.items()
    }
    json_data = json.dumps(cc_net5_payload_numpy)
    return json_data

import torch.nn.functional as F
def parse_ccnet5_ouptut(tokenizer, output_tensor):
    print(f'output_tensor: {output_tensor.shape}')
    action_type = output_tensor[:, 0]
    action_type = 'click' if int(action_type) == 0 else 'keydown'
    ref_embedding = output_tensor[:, 1:501]
    probabilities = F.softmax(ref_embedding, dim=1)
    predicted_ref = int(torch.argmax(probabilities, dim=1).to('cpu').item())

    keydowns = output_tensor[:, 501:].reshape(8, len(tokenizer.itos))
    found_keys = []
    for key in keydowns:
        probabilities = F.softmax(key.unsqueeze(0), dim=1)
        predicted_key = torch.argmax(probabilities, dim=1).to('cpu').item()
        found_keys.append(tokenizer.itos[predicted_key])
    keydowns = ''.join(found_keys).replace(tokenizer.padding_char, '')

    return action_type, predicted_ref, keydowns

import ast
def call_ccnet(rgb_input, doms, utterance, t5_output_tensor, previous_action, task_name):
    rgb_input = format_image(rgb_input)

    # format language input
    tokenized_dom = tokenizer.tokenize_dom(doms)
    tokenized_dom = np.array(tokenizer.truncate_pad_entry(tokenized_dom, 492)) # 492 is the value set for CC-NeT5 processing
    tokenized_utterance = np.array(tokenizer.truncate_pad_entry(tokenizer.tokenize_string(utterance), 16))
    tokenized_task_name = np.array(tokenizer.truncate_pad_entry(tokenizer.tokenize_string(task_name), 4))
    rgb_data, language_input = format_language_rgb_input(rgb_input, tokenized_dom, tokenized_utterance, tokenized_task_name)
    # Unsqueeze with batch size to add first dimension
    rgb_data = rgb_data.unsqueeze(0)
    language_input = language_input.unsqueeze(0)

    # format previous action (flattened tensor size 577)
    previous_action = previous_action.unsqueeze(0)
    t5_output_tensor = t5_output_tensor.unsqueeze(0)
    print(rgb_data.shape, language_input.shape, previous_action.shape, t5_output_tensor.shape)
    ccnet5_payload = prepare_ccnet5_payload(rgb_data, language_input, previous_action, t5_output_tensor)
    #ccnet5_output = infer_remote_model(ccnet5_payload, model_endpoints + '/infer_actor_normal')

    #payload = {'instruction_input': ccnet5_payload}
    headers = {'Content-Type': 'application/json'} #make_inference_normal
    response = requests.post(model_endpoints + '/make_inference_normal', data=json.dumps(ccnet5_payload), headers=headers)
    data = response.json()

    # Extract the tensor data from the loaded JSON
    tensor_data = torch.tensor(data)

    # Convert the tensor data back into a PyTorch tensor
    ccnet5_tensor = torch.tensor(tensor_data)


    ccnet5_action, ccnet5_ref, ccnet5_keydown = parse_ccnet5_ouptut(tokenizer, ccnet5_tensor)
    print(f'ccnet5 output: {ccnet5_action}, {ccnet5_ref}, {ccnet5_keydown}')

    return ccnet5_action, ccnet5_ref, ccnet5_keydown


In [24]:
# Define processing steps of a time step for the agent.
# Returns an action, and ref dictionaries over the steps.
# Pass ref dict of previous actions, empty for first step.
def observe_and_act_t5_base(observation, ref_dict, rand2ref, action_history, exp_param, task_name, env):
    # 1: Reformat Screenshot Shape
    screenshot = observation['screenshot']
    # ABLATION:
    if 'visual' in exp_param:
        screenshot = np.zeros((210, 160, 3))

    # 2: Check Utterance
    utterance = observation['utterance']

    # 3: Process DOM
    # convert elements to nested dict structure
    nested_dict = convert_to_nested_dict(observation['dom_elements'])
    # clean
    _, _, new_dom = iterate_dom(nested_dict)
    # randomize references
    ref_dict_new, _rand2ref_new = randomize_ref_dict(find_all_refs(new_dom))
    # update previous dictionaries with new observations
    ref_dict, rand2ref = update_ref2_random(ref_dict, rand2ref, ref_dict_new)
    # apply randomized references to observation DOM
    doms = attribute_random_refs_dom(new_dom, ref_dict)

    # ABLATION
    t5_output = np.zeros(10)
    if 't5_large' not in exp_param:
        # 4: Model call
        # a. T5 call
        # - Format for T5 call
        #t5_action, t5_ref, t5_keydown, done = call_T5_hierarchy(action_history, utterance, doms)
        t5_input = prepare_t5_input(action_history, utterance, doms)
        t5_output = inference_model_T5_self(t5_input)['prediction'].split(',')
        t5_action, t5_ref, t5_keydown, done = parse_t5_parts(t5_output)
        print(f't5_action: {t5_action}, t5_ref: {t5_ref}, t5_keydown: {t5_keydown}')

        # b. CC-NeT5 Call
        # format T5 into tensor for CC_Net T5
        t5_output = action2tensor(tokenizer, t5_action, t5_ref, t5_keydown)

    # ABLATION:
    previous_action = np.zeros(10) # default
    if 'previous_action' not in exp_param:
        previous_action = '' if len(action_history) == 0 else action_history[len(action_history)-1]
        previous_action = action2tensor(tokenizer, previous_action[0], previous_action[1], previous_action[2]) if previous_action != '' else np.zeros(10)


    ccnet5_action, ccnet5_ref, ccnet5_keydown = call_ccnet(screenshot, doms, utterance, torch.from_numpy(t5_output), torch.from_numpy(previous_action), task_name)

    if ccnet5_action == 'click':
        action_type = ActionTypes.CLICK_ELEMENT
    else:
        action_type = ActionTypes.TYPE_TEXT

    # Sample and Create Action
    action = env.action_space.sample()     # Template for the action.
    action["action_type"] = env.action_space_config.action_types.index(
      action_type
    )
    # Get the ref number by using the dictionary mapping random to old reference
    try:
        action["ref"] = str(rand2ref[ccnet5_ref])
    except:
        print(f'FAIL SELECTING ACTION: rand2ref: {rand2ref.keys()}, ref_dict: {ref_dict.keys()}')
        #print(doms)
        #action["ref"] = str(rand2ref[list(rand2ref.keys())[0]])
    # Add text if action is type_text
    if action_type == ActionTypes.TYPE_TEXT:
        action['text'] = ccnet5_keydown
        print(f't5_keydown: {ccnet5_keydown}')
    print(f'action to perform: {action}')

    return action, ref_dict, rand2ref

In [7]:
exp_results = {}

In [79]:
range_actions = 10 # total amount of allowed actions
max_experiments = 100
counter = 0

task_name = 'click-button-sequence'
env = gymnasium.make(f"miniwob/{task_name}")

# If the task uses the Hierarchical model
hierarchical = True

# Set up previous_action with default values
previous_action = torch.zeros(577)


while counter < max_experiments:
    if task_name not in exp_results.keys():
        exp_results[task_name] = {
            'successes': 0,
            'fails': 0,
            'unfinished': 0,
            'other': 0
        }

    plan = []

    #try:

    # Episode Data
    dom_episode = []
    action_history = []
    # Empty ref dictionaries at start of episode:
    ref_dict, rand2ref = {}, {}
    observation, info = env.reset()
    continue_flag = True # if need to keep infering

    if hierarchical:
        # Infer the plan for the hierarchical task
        #plan = call_T5_planning(observation['utterance']).split(';')
        plan = inference_model_T5_self(observation['utterance']).split(';')
        print(f'plan to solve: {plan}')
        range_actions = len(plan)

    for i in range(range_actions) or continue_flag:
        print(f'- Step {i}: {plan[i]}')

        if hierarchical:
            observation['utterance'] = plan[i]

        # Process observation and return Action + Ref Dicts
        action, ref_dict, rand2ref = observe_and_act_t5_base(observation, ref_dict, rand2ref, action_history)
        # Perform action on environment
        observation, reward, terminated, truncated, info = env.step(action)

        # important to translate the action type below
        action_type = 0 if action['action_type'] == 8 else 1
        keydown = '' if action['text'] == 'q[]' or action_type == 0 else action['text'].replace('q[', '').replace(']', '')
        # todo: use ref_dict to translate previous action_ref
        action_history.append([action_type, ref_dict[int(action['ref'])], keydown])

        # Episode is over
        if terminated:
            print(reward, terminated)

            if reward > 0:
                # todo: save successful episode:
                # dom, actions, refs, ref_dict to transform doms and actions
                # rewards etc
                print('Success')
                exp_results[task_name]['successes'] += 1
            else:
                print('Fail')
                exp_results[task_name]['fails'] += 1
            break


        time.sleep(0.05)
    #except Exception as e:
    #    print(f'Error loop: {e}')

    if not terminated:
        exp_results[task_name]['unfinished'] += 1

    counter += 1



env.close()
print(exp_results)

/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/gymnasium/envs/registration.py:586: UserWarning: WARN: Using the latest versioned environment `miniwob/click-button-sequence-v1` instead of the unversioned environment `miniwob/click-button-sequence`.
  logger.warn(


AttributeError: 'dict' object has no attribute 'split'

In [41]:
action_history

[]

In [30]:
def run_benchmark(exp_param):
    exp_results = {}

    # Mega Loop

    range_actions = 10 # total amount of allowed actions
    max_experiments = 100
    hierarchical = True

    # ABLATION STUDY
    if 't5_large' in exp_param:
        hierarchical = False

    task_names = [
    'click-button',
    'click-checkboxes-large',
        'click-checkboxes-soft',
    'click-checkboxes-transfer',
    'click-checkboxes',
    'click-collapsible-2',
    'click-collapsible',
    'click-color',
    'click-dialog-2',
    'click-dialog',
    'click-link',
    'click-menu-2',
    'click-menu',
    'click-option',
    'click-pie',
    'click-scroll-list',
    'click-shades',
    'click-shape',
    'click-tab-2-easy',
        'click-tab',
        'click-test-2',
        'click-test-transfer',
        'click-widget',
        'count-shape',
        'enter-text',
        'identify-shape',
        'navigate-tree',
        'use-spinner',
    ]


    for task_name in task_names:
        print(exp_results)

        counter = 0

        env = gymnasium.make(f"miniwob/{task_name}")

        # If the task uses the Hierarchical model


        while counter < max_experiments:

            try:

                print(f'TASK NAME: {task_name}')
                if task_name not in exp_results.keys():
                    exp_results[task_name] = {
                        'successes': 0,
                        'fails': 0,
                        'unfinished': 0,
                        'other': 0
                    }

                plan = []

                #try:

                # Episode Data
                dom_episode = []
                action_history = []
                # Empty ref dictionaries at start of episode:
                ref_dict, rand2ref = {}, {}
                observation, info = env.reset()
                continue_flag = True # if need to keep infering

                if hierarchical:
                    # Infer the plan for the hierarchical task
                    #plan = call_T5_planning(observation['utterance']).split(';')
                    plan = 'Devise a plan for the following instruction: ' + observation['utterance']
                    plan = inference_model_T5_self(plan)['prediction']
                    print(f'plan to solve: {plan}')
                    plan = plan.split(';')
                    #range_actions = len(plan)

                for i in range(range_actions):
                    if i < len(plan):
                        print(f'- Step {i}: {plan[i]}')
                    else:
                        print(f'- Step {i}')

                    if hierarchical:
                        if i < len(plan):
                            observation['utterance'] = plan[i]
                        elif len(plan) == 0:
                            ''
                        else:
                            observation['utterance'] = plan[len(plan)-1]

                    # Process observation and return Action + Ref Dicts
                    action, ref_dict, rand2ref = observe_and_act_t5_base(observation, ref_dict, rand2ref, action_history, exp_param, task_name, env)
                    # Perform action on environment
                    observation, reward, terminated, truncated, info = env.step(action)

                    # important to translate the action type below
                    action_type = 0 if action['action_type'] == 8 else 1
                    keydown = '' if action['text'] == 'q[]' or action_type == 0 else action['text'].replace('q[', '').replace(']', '')
                    # todo: use ref_dict to translate previous action_ref # ref_dict[
                    action_history.append([action_type, int(action['ref']), keydown])

                    # Episode is over
                    if terminated:
                        print(reward, terminated)

                        if reward > 0:
                            # todo: save successful episode:
                            # dom, actions, refs, ref_dict to transform doms and actions
                            # rewards etc
                            print('Success')
                            exp_results[task_name]['successes'] += 1
                        else:
                            print('Fail')
                            exp_results[task_name]['fails'] += 1
                        break


                    time.sleep(0.05)
                #except Exception as e:
                #    print(f'Error loop: {e}')

                if not terminated:
                    exp_results[task_name]['unfinished'] += 1

                counter += 1
            except Exception as e:
                print(f'ERROR OUTER LOOP TRY: {e}, continue...')
                continue

        env.close()
        print(exp_results)

    return exp_results


In [31]:
#'visual']#,
exp_params = ['previous_action', 't5_large']

exp_results_full = {}

for exp_param in exp_params:
    results = run_benchmark(exp_param)
    exp_results_full[exp_param] = results


{}


/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/gymnasium/envs/registration.py:586: UserWarning: WARN: Using the latest versioned environment `miniwob/click-button-v1` instead of the unversioned environment `miniwob/click-button`.
  logger.warn(


TASK NAME: click-button
plan to solve: Click on the "Okay" button. ;
- Step 0: Click on the "Okay" button. 
t5_action: click, t5_ref: 8, t5_keydown: 
(512,)
torch.Size([1, 3, 210, 160]) torch.Size([1, 512]) torch.Size([1, 10]) torch.Size([1, 10])


/var/folders/z7/8t7cnys53zng5b98fknc2qb00000gn/T/ipykernel_25766/4219090687.py:85: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  ccnet5_tensor = torch.tensor(tensor_data)


output_tensor: torch.Size([1, 13229])
ccnet5 output: click, 8, 
action to perform: OrderedDict([('action_type', 8), ('coords', array([ 5.527437, 95.709564], dtype=float32)), ('field', 0), ('key', 66), ('ref', '7'), ('text', 'Rdd|!^IM"n7*E]["tuQjoY)*Zm^}1eB5*6xsWa\\_^P+`a0qCO6vi(xw.MxKB6w')])
- Step 1: 
t5_action: click, t5_ref: 8, t5_keydown: 
(512,)
torch.Size([1, 3, 210, 160]) torch.Size([1, 512]) torch.Size([1, 10]) torch.Size([1, 10])
output_tensor: torch.Size([1, 13229])
ccnet5 output: click, 8, 
action to perform: OrderedDict([('action_type', 8), ('coords', array([ 31.839775, 152.65947 ], dtype=float32)), ('field', 8), ('key', 30), ('ref', '7'), ('text', "O]'{LM")])
- Step 2
t5_action: click, t5_ref: 7, t5_keydown: 
(512,)
torch.Size([1, 3, 210, 160]) torch.Size([1, 512]) torch.Size([1, 10]) torch.Size([1, 10])
output_tensor: torch.Size([1, 13229])
ccnet5 output: click, 7, 
action to perform: OrderedDict([('action_type', 8), ('coords', array([11.90849 , 78.215355], dtype=float32)

...

output_tensor: torch.Size([1, 13229])
ccnet5 output: click, 28, 
FAIL SELECTING ACTION: rand2ref: dict_keys([3, 5, 7, 2, 8, 10, 4, 11, 6, 9, 1]), ref_dict: dict_keys([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11])
action to perform: OrderedDict([('action_type', 8), ('coords', array([86.737946, 28.53155 ], dtype=float32)), ('field', 8), ('key', 91), ('ref', 254353), ('text', ">>WUJ'S^*5Y7Qtsd6>")])
- Step 6
(512,)
torch.Size([1, 3, 210, 160]) torch.Size([1, 512]) torch.Size([1, 10]) torch.Size([1, 10])


output_tensor: torch.Size([1, 13229])
ccnet5 output: click, 28, 
FAIL SELECTING ACTION: rand2ref: dict_keys([3, 5, 7, 2, 8, 10, 4, 11, 6, 9, 1]), ref_dict: dict_keys([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11])
action to perform: OrderedDict([('action_type', 8), ('coords', array([33.80019 , 33.237385], dtype=float32)), ('field', 13), ('key', 64), ('ref', 666435), ('text', '"GOY8-~tc.=T)E$Is];6*"E\\z)vcT7jhMm%AxztJ7L~>4L>j?PvWW/Om}qm(@8t=')])
- Step 7
(512,)
torch.Size([1, 3, 210, 160]) torch.Size([1, 512]) torch.Size([1, 10]) torch.Size([1, 10])


output_tensor: torch.Size([1, 13229])
ccnet5 output: click, 28, 
FAIL SELECTING ACTION: rand2ref: dict_keys([3, 5, 7, 2, 8, 10, 4, 11, 6, 9, 1]), ref_dict: dict_keys([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11])
action to perform: OrderedDict([('action_type', 8), ('coords', array([145.95517 ,   9.849886], dtype=float32)), ('field', 7), ('key', 9), ('ref', 632271), ('text', 'hw%KyFi`u?9x1)e1NpaG*>H?xYsTczI6%]PqnZujC@`p^Cp-e_%t')])
- Step 8
(512,)
torch.Size([1, 3, 210, 160]) torch.Size([1, 512]) torch.Size([1, 10]) torch.Size([1, 10])


output_tensor: torch.Size([1, 13229])
ccnet5 output: click, 28, r
FAIL SELECTING ACTION: rand2ref: dict_keys([3, 5, 7, 2, 8, 10, 4, 11, 6, 9, 1]), ref_dict: dict_keys([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11])
action to perform: OrderedDict([('action_type', 8), ('coords', array([144.41673 , 110.606804], dtype=float32)), ('field', 4), ('key', 41), ('ref', 200220), ('text', "%D5R`,/}c/dZFoc9DKG<_/|kl/lkRi$LjtI|]Iewd=5'{>")])
- Step 9
(512,)
torch.Size([1, 3, 210, 160]) torch.Size([1, 512]) torch.Size([1, 10]) torch.Size([1, 10])


output_tensor: torch.Size([1, 13229])
ccnet5 output: click, 28, r
FAIL SELECTING ACTION: rand2ref: dict_keys([3, 5, 7, 2, 8, 10, 4, 11, 6, 9, 1]), ref_dict: dict_keys([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11])
action to perform: OrderedDict([('action_type', 8), ('coords', array([52.825268, 35.86052 ], dtype=float32)), ('field', 16), ('key', 37), ('ref', 421990), ('text', 'c9`9h1>na*Xrec&,Ta8%ZxMcyMUtPnmJfn_]F+Ny@*hTVjr')])
{'click-button': {'successes': 0, 'fails': 0, 'unfinished': 25, 'other': 0}, 'click-checkboxes-large': {'successes': 0, 'fails': 25, 'unfinished': 0, 'other': 0}, 'click-checkboxes-soft': {'successes': 0, 'fails': 0, 'unfinished': 25, 'other': 0}, 'click-checkboxes-transfer': {'successes': 0, 'fails': 0, 'unfinished': 25, 'other': 0}, 'click-checkboxes': {'successes': 0, 'fails': 0, 'unfinished': 25, 'other': 0}, 'click-collapsible-2': {'successes': 0, 'fails': 0, 'unfinished': 25, 'other': 0}, 'click-collapsible': {'successes': 0, 'fails': 0, 'unfinished': 25, 'other': 0}

In [1]:
exp_results_full

NameError: name 'exp_results_full' is not defined

In [ ]:
exp_results

In [51]:
# 'click-button',
   # 'click-checkboxes-large',
   #     'click-checkboxes-soft',
   # 'click-checkboxes-transfer',
   # 'click-checkboxes',
   # 'click-collapsible-2',
   # 'click-collapsible',
   # 'click-color',
   # 'click-dialog-2',
   # 'click-dialog',
   # 'click-link',

0.43499999999999994